# Data Profiling and Preparation
## Chapter II: Data Preparation

---

# Importing libraries

In [0]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
from pytz import timezone

pd.options.display.max_columns = None

# Reading example data

In [0]:
# Read data
telco_churn = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/Telco-Churn-dirty.csv", na_values=" ")
hr_data = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/HR-Employee-Attrition.csv")
weather_data = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/hourly_weather.csv")
gov_exp_data = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/gov_expenditure_education.csv")
superstore = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/Superstore.csv", index_col="Row ID")

# Data Cleansing

## Missing data

Using DataFrame's built-in function

In [0]:
telco_churn.isnull().any()

In [0]:
telco_churn.info()

Using `Missingno` library

In [0]:
import missingno as msno

In [0]:
msno.bar(telco_churn) 

### Investigate the cause of missing data

In [0]:
telco_churn[telco_churn["TotalCharges"].isna()][["tenure", "TotalCharges"]]

### Fill missing value in `TotalCharges` using `.fillna()`

In [0]:
telco_churn["TotalCharges"] = telco_churn["TotalCharges"].fillna(0)

In [0]:
telco_churn.isnull().any()

### Drop rows will missing value in `Churn` using `.dropna()`

In [0]:
telco_churn.dropna(subset=["Churn"], inplace=True)

In [0]:
msno.bar(telco_churn) 

## Invalid data

In [0]:
telco_churn.describe()

In [0]:
telco_churn[telco_churn["tenure"]<0]

### Select a row with non-negative `tenure`

In [0]:
telco_churn = telco_churn[telco_churn["tenure"]>=0]
telco_churn.describe()

## Fragmented

In [0]:
pd.crosstab(telco_churn["InternetService"], columns="Count")

### Merge `ADSL` into `DSL`

In [0]:
telco_churn["InternetService"].replace("ADSL", "DSL", inplace=True)

In [0]:
pd.crosstab(telco_churn["InternetService"], columns="Count")

## Outliers

### Check for outliers

In [0]:
sns.set_style("whitegrid")

In [0]:
hr_data.describe()

In [0]:
plt.figure(figsize=(12,4))
sns.boxplot(data=hr_data, x="MonthlyIncome", y="JobRole")
plt.show()

### Remove rows with outliers in `MonthlyIncome` of `Sales Representative`

In [0]:
outlier_threshold = hr_data[hr_data["JobRole"]=="Sales Representative"]["MonthlyIncome"].quantile(0.95)
print(f"Outlier threshold: {outlier_threshold}")

In [0]:
filter_idx = hr_data[(hr_data["JobRole"]=="Sales Representative") & (hr_data["MonthlyIncome"]>outlier_threshold)].index
print(filter_idx)

In [0]:
hr_data1 = hr_data[~hr_data.index.isin(filter_idx)]

In [0]:
plt.figure(figsize=(12,4))
sns.boxplot(data=hr_data1, x="MonthlyIncome", y="JobRole")
plt.show()

### Clipping outliers in `MonthlyIncome` of `Sales Representative`

In [0]:
clip_idx = hr_data[hr_data["JobRole"]=="Sales Representative"].index

In [0]:
hr_data.loc[clip_idx, "MonthlyIncome"] = hr_data.loc[clip_idx, "MonthlyIncome"].clip(upper=outlier_threshold)

In [0]:
plt.figure(figsize=(12,4))
sns.boxplot(data=hr_data, x="MonthlyIncome", y="JobRole")
plt.show()

# Challenge #1

หาข้อผิดพลาดที่เกิดขึ้นในข้อมูลต่อไปนี้ จากนั้นกำหนด Correction Logic และแก้ไขข้อมูลให้ถูกต้อง 
- Flights
- HR Data
- ATM Data 

In [0]:
flight_data = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/Flight_flights.csv",
                          index_col=0, dtype={"dep_time":str,
                                              "sched_dep_time":str,
                                              "arr_time":str,
                                              "sched_arr_time":str,
                                              "flight":str
                                              }
                          )
hr_data = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/HR-Employee-Attrition.csv")
atm_data = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/ATM_data.csv")

# Data Preprocessing

## Data enrichment

### Calculation

In [0]:
superstore.head()

In [0]:
# Calculate UnitSale
superstore["UnitSales"] = superstore["Sales"] / superstore["Quantity"]

In [0]:
superstore[["Order ID", "Product Name", "Sales", "Quantity", "UnitSales"]]

### Merging (Join)

In [0]:
# Read data
flight_flights = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/Flight_flights.csv", index_col=0)
flight_airlines = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/Flight_airlines.csv", index_col=0)

In [0]:
flight_flights.head()

In [0]:
flight_airlines.head()

In [0]:
flights = flight_flights.merge(flight_airlines, on="carrier", how="left")
flights[["carrier", "flight", "name"]]

### Concatenate (Union)

In [0]:
# Read data
housedata_b1 = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/HousingData_B-001.csv")
housedata_b2 = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/HousingData_B-002.csv")

In [0]:
housedata_b1.head()

In [0]:
housedata_b2.head()

In [0]:
housedata = pd.concat([housedata_b1, housedata_b2], axis=0)
housedata

## Summarization

### `.describe()`

In [0]:
superstore.describe()

### Simple aggregation

In [0]:
superstore.agg(Total_order=("Order ID", "nunique"))

### Group aggregation

In [0]:
superstore.groupby("Category").agg(Total_sales=("Sales", "sum"),
                                   Total_profit=("Profit", "sum"),
                                   )

## Reshaping data

### Long to wide – multiple rows per unit

In [0]:
weather_data.head(20)

In [0]:
weather_data["date"] = weather_data["datetime"].str[:10]

In [0]:
weather_data.pivot_table(index="date",
                         columns="city",
                         values="temp_c",
                         aggfunc="mean",
                         fill_value=0
                         )

### Wide to long

In [0]:
gov_exp_data.head()

In [0]:
import re
value_cols = [x for x in gov_exp_data.columns if re.match(r"\d{4}", x)]

In [0]:
gov_exp_data.melt(id_vars="Country Name",
                  value_vars=value_cols,
                  value_name="Percent",
                  var_name="Year"
                  )

## Working with Date and Time data

### Datetime in Python

Create datetime object

In [0]:
# Using datetime function
my_date = datetime(2024, 9, 3, 12, 30)
print(my_date)

In [0]:
# Using .strptime to create datetime object from string
date_string = "3/09/2024 12:30"

my_date = datetime.strptime(date_string, "%d/%m/%Y %H:%M")
print(my_date)

In [0]:
# Timezone-aware datetime
my_date = datetime(2024, 9, 3, 12, 30)
# IANA Timezone code
my_date = timezone("Asia/Bangkok").localize(my_date)
print(my_date)

In [0]:
# Convert datetime to different timezone
my_date.astimezone(timezone("Asia/Tokyo"))

Displaying datetime

In [0]:
# Create formatted time string from datetime object
my_date.strftime("%a %d-%B-%Y %H:%M:%S")

### Datetime in Pandas

Checking for datetime data in DataFrame

In [0]:
superstore.sample(5)

In [0]:
superstore.info()

Convert string column into datetime

In [0]:
superstore["Order Date"] = pd.to_datetime(superstore["Order Date"],
                                          format="%Y-%m-%d",
                                          errors="coerce"
                                          )
superstore["Ship Date"] = pd.to_datetime(superstore["Ship Date"],
                                          format="%Y-%m-%d",
                                          errors="coerce"
                                          )

Check data type again

In [0]:
superstore.info()

### Filter DataFrame with datetime

#### Filtering date

Datetime column can be also be use in conditional filtering.  
Normally, datetime can only be compared with another datetime object.  
But in Pandas, the string passed in conditional filtering on datetime column will be automatically converted to datetime object.

In [0]:
# Filter order that placed in the year 2013
superstore[(superstore["Order Date"] >= "2013-01-01") & (superstore["Order Date"] < "2014-01-01")]

#### More complex filtering

If you want to filter with more complex conditions. For example: data that occurs on weekend (Saturday or Sunday). The easiest way is to extract the information that you want to filter into new columns, and use that column to filtter.

**Example 1: Filter only data that occurs on weekend**

Format string `%a` returns the shorterned name of the day (Sun, Mon, Tue,...).  
You can also use `%w` which return day of week index, where Sunday is 0 and Saturday is 6.

In [0]:
superstore["day_of_week"] = superstore["Order Date"].dt.strftime("%a")
superstore[superstore["day_of_week"].isin(["Sun", "Sat"])]

**Example 2: Filter only data that occurs on day 1 and 16 of every month**

Format string `%d` returns the day of month.

In [0]:
superstore["day_of_month"] = superstore["Order Date"].dt.strftime("%d")
superstore[superstore["day_of_month"].isin(["1", "16"])]

### Timedelta

The subtraction of 2 datetime object will result in a `Timedelta` object

In [0]:
date_1 = datetime(2023, 7, 24, 12, 30)
date_2 = datetime.today()

In [0]:
diff = date_2 - date_1
print(diff)

In [0]:
type(diff)

To get exact seconds from timedelta, use `.total_seconds()`

In [0]:
diff.total_seconds()

This can then be used to convert into other time format. For example:

In [0]:
diff.total_seconds() // 60

In [0]:
# Convert to minutes
diff.total_seconds() // 60

In [0]:
# Convert to hours
diff.total_seconds() // (60*60)

In [0]:
# Convert to days
diff.total_seconds() // (60*60*24)

If we subtract `Order Date` from `Ship Date`, we will get the duration that the order is being prepared until it is shipped.

In [0]:
superstore["Process Time"] = superstore["Ship Date"] - superstore["Order Date"]
superstore[["Order ID", "Order Date", "Ship Date", "Process Time"]].head()

### Relativedelta

In [0]:
my_date = datetime.today()
my_date = timezone("Asia/Bangkok").localize(my_date)
print(my_date)

In [0]:
my_date + relativedelta(days=3, hours=4)

In [0]:
my_date - relativedelta(days=7)

## Profiling

In [0]:
superstore = pd.read_csv("/Workspace/Users/supawit.somsa@kmutt.ac.th/Superstore.csv", index_col="Row ID")

superstore["Order Date"] = pd.to_datetime(superstore["Order Date"],
                                          format="%Y-%m-%d",
                                          errors="coerce"
                                          )
superstore["Ship Date"] = pd.to_datetime(superstore["Ship Date"],
                                          format="%Y-%m-%d",
                                          errors="coerce"
                                          )

In [0]:
superstore.head()

### Recency

Calculate the duration from last purchase of each customer

Let the max date in this dataset be our reference date

In [0]:
reference_date = max(superstore["Order Date"])
print(reference_date)

In [0]:
(reference_date - superstore["Order Date"])

In [0]:
(reference_date - superstore["Order Date"]).dt.days

Define a function to calculate time since last purchase

In [0]:
def recency(x):
    current_max = x.max()
    duration = reference_date - current_max
    return duration.days

In [0]:
superstore[superstore["Customer ID"]=="DV-13045"]["Order Date"]

In [0]:
(reference_date - superstore[superstore["Customer ID"]=="DV-13045"]["Order Date"].max()).days

In [0]:
recency(superstore[superstore["Customer ID"]=="DV-13045"]["Order Date"])

Apply function to each customer

In [0]:
superstore.groupby(["Customer ID"]).agg(Recency=("Order Date", recency))

### Frequency

Count how many times the customer made purchase

In [0]:
superstore.groupby(["Customer ID"]).agg(Frequency=("Order ID", "nunique"))

## Monetary

Total amount paid by customer

In [0]:
superstore.groupby(["Customer ID"]).agg(Monetary=("Sales", "sum"))

## Put it all together

In [0]:
superstore.groupby(["Customer ID"]).agg(Recency=("Order Date", recency),
                                        Frequency=("Order ID", "nunique"),
                                        Monetary=("Sales", "sum")
                                        )

# Challenge #2

1. ทดลองทำ Profiling Analysis ในระดับ Region โดยให้กำหนดตัวแปรตามที่สนใจ เช่น
  - จำนวนคำสั่งซื้อทั้งหมด
  - รายได้จากการขายแยกตามประเภทของสินค้า

2. ทดลองคิดตัวแปรอื่นๆ ของ Profiling ในระดับ Customer


---